# Load data

Uncomment the code bellow to download data.

In [1]:
#!wget https://github.com/hetio/hetionet/raw/main/hetnet/matrix/hetionet-v1.0.hetmat.zip
#!7za x hetionet-v1.0.hetmat.zip -odata

In [2]:
import torch
from RelationalLearning.DataLoader import load_graph

graph = load_graph()

dev = "cuda" if torch.cuda.is_available() else "cpu"


('Disease', 'presents', 'Symptom')
('Anatomy', 'downregulates', 'Gene')
('Compound', 'binds', 'Gene')
('Disease', 'associates', 'Gene')
('Gene', 'participates', 'Cellular Component')
('Gene', 'participates', 'Pathway')
('Gene', 'regulates', 'Gene')
('Disease', 'localizes', 'Anatomy')
('Anatomy', 'upregulates', 'Gene')
('Compound', 'palliates', 'Disease')
('Compound', 'causes', 'Side Effect')
('Gene', 'participates', 'Biological Process')
('Compound', 'upregulates', 'Gene')
('Compound', 'resembles', 'Compound')
('Gene', 'covaries', 'Gene')
('Gene', 'interacts', 'Gene')
('Disease', 'upregulates', 'Gene')
('Pharmacologic Class', 'includes', 'Compound')
('Gene', 'participates', 'Molecular Function')
('Compound', 'downregulates', 'Gene')
('Disease', 'downregulates', 'Gene')
('Disease', 'resembles', 'Disease')
('Anatomy', 'expresses', 'Gene')
('Compound', 'treats', 'Disease')


## Initiliaze node features

In [3]:
from RelationalLearning.utils import ntype_one_hot_init

ntype_one_hot_init(graph)
in_feature_size = 11

## Split dataset

In [ ]:
from RelationalLearning.DataLoader import remove_random_edges, abbr_map

input_graph, removed_eids = remove_random_edges(graph, 0.1, [abbr_map["CcSE"]])
len(removed_eids[("Compound", "causes", "Side Effect")])

In [6]:
from RelationalLearning.DataLoader import HetioNetDataset, DownstreamDataset
from RelationalLearning.utils import dec_pert
import torch

import random
import dgl
import numpy as np

random.seed(42)
dgl.seed(42)
np.random.seed(42)
torch.manual_seed(42)
torch.cuda.manual_seed_all(42)

pretext_enc_dataset = HetioNetDataset(input_graph)
pretext_dec_dataset = HetioNetDataset(input_graph, perturbation_fn=dec_pert(.2))

downstream_enc_dataset = HetioNetDataset(input_graph, perturbation_fn=lambda x: x)
train_downstream_dataset = DownstreamDataset(graph, removed_eids, n_negative_samples=1, test_ratio=0.1, split_type="train")
val_downstream_dataset = DownstreamDataset(graph, removed_eids, n_negative_samples=1, test_ratio=0.1, split_type="val")
test_downstream_dataset = DownstreamDataset(graph, removed_eids, n_negative_samples=1, test_ratio=0.1, split_type="test")

train_downstream_loader = torch.utils.data.DataLoader(train_downstream_dataset, batch_size=256, shuffle=True)
val_downstream_loader = torch.utils.data.DataLoader(val_downstream_dataset, batch_size=len(val_downstream_dataset), shuffle=False)
test_downstream_loader = torch.utils.data.DataLoader(test_downstream_dataset, batch_size=len(test_downstream_dataset), shuffle=False)

# Models' definitions

In [7]:

from torch import nn
from dgl.nn.pytorch import HeteroGraphConv, SAGEConv
from torch.nn import Linear, Sequential, ReLU, Softmax
import torch.nn.functional as F

class Encoder(nn.Module):
    def __init__(self, graph, in_size, n_feat) -> None:
        super(Encoder, self).__init__()
        convolutions_config_1 = {}
        for etype in set(graph.etypes):
            convolutions_config_1[etype] = SAGEConv(in_size, n_feat, "gcn", feat_drop=0.5)

        convolutions_config_2 = {}
        for etype in set(graph.etypes):
            convolutions_config_2[etype] = SAGEConv(n_feat, n_feat, "pool", feat_drop=0.5)

        # convolution layers for node representation updates
        self.conv1 = HeteroGraphConv(convolutions_config_1, aggregate="mean")
        self.conv2 = HeteroGraphConv(convolutions_config_2, aggregate="mean")

    def forward(self, g, in_feat):
        # apply first conv layer on node representations
        h_n = self.conv1(g, in_feat)

        # apply relu and second conv layer on node representations
        h_n = self.conv2(g, {ntype: F.relu(h_i) for ntype, h_i in h_n.items()})

        return h_n


class PretextDecoder(torch.nn.Module):
    def __init__(self, graph, in_size, n_feat) -> None:
        super(PretextDecoder, self).__init__()

        # feed-forward network for each edge type
        self.etype_mlp = torch.nn.ModuleDict()
        for etype in set(graph.etypes):
            self.etype_mlp[etype] = Sequential(
                Linear(in_size, n_feat),
                nn.BatchNorm1d(n_feat),
                nn.Dropout(),
                Linear(n_feat, n_feat),
                ReLU(),
                Linear(n_feat, 1)
            )

    def forward(self, g, in_feat):
        with g.local_scope():
            # Assign the input features to the nodes
            g.ndata["f"] = in_feat

            # Compute the score for each edge type using the corresponding MLP
            for rel in g.canonical_etypes:
                mlp = self.etype_mlp[rel[1]]
                g.apply_edges(lambda edges: {"scores": mlp(torch.cat((edges.src["f"], edges.dst["f"]), 1))}, etype=rel)

            return g.edata["scores"]


class DownstreamDecoder(torch.nn.Module):
    def __init__(self, in_size, n_feat) -> None:
        super(DownstreamDecoder, self).__init__()

        self.mlp = Sequential(
            Linear(in_size, n_feat), 
            nn.Dropout(),
            nn.ReLU(),
            Linear(n_feat, 2)
        )

    def forward(self, src_nodes, dst_nodes, in_feat):
        h = [torch.cat([in_feat["Compound"][src_nodes[i].item()], in_feat["Side Effect"][dst_nodes[i].item()]])
             for i in range(len(src_nodes))]

        pred = self.mlp(torch.stack(h))

        return pred

# Training

In [8]:
embeddings_size = 32

encoder = Encoder(graph=input_graph,
                  in_size=in_feature_size,
                  n_feat=embeddings_size)

## Pretext

In [ ]:
import itertools
from RelationalLearning.utils import train_pretext, compute_pretext_loss

pretext_decoder = PretextDecoder(graph=input_graph,
                                 in_size=embeddings_size * 2,
                                 n_feat=64)

optimizer = torch.optim.Adam(
    itertools.chain(encoder.parameters(), pretext_decoder.parameters()),
    lr=0.01
)

train_pretext(encoder=encoder,
              decoder=pretext_decoder,
              enc_dataset=pretext_enc_dataset,
              dec_dataset=pretext_dec_dataset,
              optimizer=optimizer,
              loss_fn=compute_pretext_loss,
              epochs=150,
              dev=dev)

## Downstream

In [ ]:
from RelationalLearning.utils import train_downstream

downstream_decoder = DownstreamDecoder(in_size=embeddings_size * 2,
                                       n_feat=32)

optimizer = torch.optim.Adam(
    itertools.chain(encoder.parameters(), downstream_decoder.parameters()),
    lr=0.002
)

train_downstream(encoder=encoder,
                 decoder=downstream_decoder,
                 enc_dataset=downstream_enc_dataset,
                 dec_dataset=train_downstream_loader,
                 val_dataset=val_downstream_loader, 
                 optimizer=optimizer,
                 epochs=100,
                 dev=dev)

# Evaluation

In [ ]:
from RelationalLearning.utils import evaluate, plot_side_effects_mat

encoder.eval()
downstream_decoder.eval()

evaluate(test_downstream_loader, encoder.to(dev), downstream_decoder.to(dev), input_graph.to(dev), dev, plot=True, plot_fun=plot_side_effects_mat)